In [1]:
# Copyright 2025 Keysight Technologies Inc.

In [2]:
import keysight.qcs as qcs
import numpy as np

In [3]:
# initialize a constant envelope
envelope = qcs.ConstantEnvelope()
dc_wav = qcs.DCWaveform(duration=2, envelope=envelope, amplitude=1)

# instantiate an empty program
program = qcs.Program()

# instantiate an awg channel
awg = qcs.Channels(range(1), "awg_channel")

# add the envelope to the program
program.add_waveform(dc_wav, awg)

# render
program.render(sample_rate=1e3)

In [4]:
# initialize a Gaussian
envelope = qcs.GaussianEnvelope(num_sigma=2)
dc_wav = qcs.DCWaveform(32e-9, envelope, 1)

# initialize the program and add the envelope
program = qcs.Program()
program.add_waveform(dc_wav, awg)

# render
program.render()

In [5]:
# initialize parameters
duration = qcs.Scalar("duration", value=32e-9, dtype=float)
amplitude = qcs.Scalar("amplitude", value=0.8, dtype=float)
rise = qcs.Scalar("rise", value=8e-9, dtype=float)

# initialize a Gaussian DC Waveform
dc_wav = qcs.DCWaveform(
    duration=2 * rise, envelope=qcs.GaussianEnvelope(), amplitude=amplitude
)

# initialize the program and add the flattop using the to_flattop method
program = qcs.Program()
program.add_waveform(dc_wav.to_flattop(duration), awg)

# render
program.render()

In [6]:
duration.value = 64e-9
amplitude.value = 0.6
rise.value = 20e-9

# render
program.render()

In [7]:
base_envelope = qcs.GaussianEnvelope(num_sigma=5)
envelope = qcs.DerivativeEnvelope(base_envelope)
dc_wav = qcs.DCWaveform(2, envelope, 0.7)

# initialize the program and add the envelope
program = qcs.Program()
program.add_waveform(dc_wav, awg)

# render
program.render(sample_rate=1e3)

In [8]:
# initialize a 30ns Gaussian RF Waveform at 5GHz
gauss = qcs.RFWaveform(
    duration=30e-9, envelope=qcs.GaussianEnvelope(), amplitude=0.8, rf_frequency=5e9
)

# initialize the program and add the drag pulse with a coefficient of 0.05
program = qcs.Program()
program.add_waveform(gauss.drag(0.05), awg)

# render
program.render(sample_rate=5e9, plot_imaginary=True)

In [9]:
duration = 3
rise_time = 0.5
fall_time = 1
amplitude = 0.6

# specify the samples for linear interpolation
times = [0, rise_time, duration - fall_time, duration]
samples = [0, amplitude, amplitude, 0]

# initialize the envelope
envelope = qcs.ArbitraryEnvelope(times, samples)
dc_wav = qcs.DCWaveform(duration, envelope, amplitude)

# initialize the program and add the envelope
program = qcs.Program()
program.add_waveform(dc_wav, awg)

# render
program.render(sample_rate=1e3)

In [10]:
# define the sech envelope
def sech(times, A, sigma):
    return A / np.cosh((times - times[-1] / 2) / sigma)


A = 0.45
sigma = 0.15

# initialize the envelope
envelope = qcs.ArbitraryEnvelope.sample(lambda t: sech(t, A, sigma), n_samples=100)

duration = 1
dc_wav = qcs.DCWaveform(duration, envelope, 1)

# initialize the program and add the envelope
program = qcs.Program()
program.add_waveform(dc_wav, awg)

program.render(sample_rate=1e3)

In [11]:
# define the sine envelope
def sine(input_times, amplitude, freq, phase):
    return amplitude * np.sin(2 * np.pi * freq * input_times + phase)


amplitude = 0.4
phase = 0
freq = 0.5

# initialize the envelope
envelope = qcs.ArbitraryEnvelope.sample(
    lambda t: sine(t, amplitude, freq, phase), n_samples=100
)

duration = 1
dc_wav = qcs.DCWaveform(duration, envelope, amplitude)

# initialize the program and add the envelope
program = qcs.Program()
program.add_waveform(dc_wav, awg)

program.render(sample_rate=1e3)